In [40]:
import numpy as np
import pandas as pd
import networkx as nx
import matplotlib.pyplot as plt
import os

In [41]:
#read the data
data = pd.read_csv('cleaned_data.csv')

In [ ]:
unique_primary_industry_sectors = data['Primary Industry Sector'].unique()
unique_primary_industry_sectors

In [43]:
def create_graph(data):
    # Convert to DataFrame
    df = pd.DataFrame(data)

    # Create a graph
    G = nx.Graph()

    # Add nodes and edges
    for _, row in df.iterrows():
        company = row['Companies']
        industry = row['Primary Industry Sector']
        partner = row['Partners'].split(', ')  # Split partner by ", "

        G.add_node(company, type=industry)  # Add company as a node
        for investor in partner:
            G.add_node(investor, type='investor')  # Add investor as a node
            G.add_edge(company, investor)  # Connect company with partner

    return G

In [ ]:
sector_colors = {
    'Information Technology': 'blue',
    'Business Products and Services (B2B)': 'green',
    'Healthcare': 'red',
    'Consumer Products and Services (B2C)': 'purple',
    'Energy': 'orange',
    'Financial Services': 'yellow',
    'Materials and Resources': 'brown'
}

sector_colors

In [45]:
def save_graph(G, filename , output_folder=''):
    # Draw the graph
    fig = plt.figure(figsize=(100, 60))
    pos = nx.spring_layout(G, seed=42)  # Layout for positioning nodes
    node_colors = [
        sector_colors[G.nodes[n]['type']] if G.nodes[n]['type'] in sector_colors else 'lightgreen'
        for n in G.nodes
    ]

    nx.draw(G, pos, with_labels=True, node_color=node_colors, edge_color='gray', node_size=100, font_size=2, font_weight='bold')

    plt.title(filename)

    # Draw legend
    handles = [plt.Line2D([0], [0], marker='o', color='w', markerfacecolor=color, markersize=10, label=sector)
               for sector, color in sector_colors.items()]
    plt.legend(title='Primary Industry Sector', handles=handles, loc='lower left')

    #plt.show()
    
    # Save the graph in the output folder
    output_folder = 'output/'+output_folder+'/'
    if not os.path.exists(output_folder):
        os.makedirs(output_folder)
    filename = output_folder + filename
    
    nx.write_gexf(G, filename + '.gexf')  # save as gexf

    # save as png
    fig.savefig(filename + '.png', dpi=300)

In [ ]:
df_companies_partners = data[['Companies', 'Partners', 'Primary Industry Sector']]

df_companies_partners

In [ ]:
xavier_niel_data = df_companies_partners[df_companies_partners['Partners'].str.contains('Xavier Niel')]
xavier_niel_data

In [48]:
G = create_graph(xavier_niel_data)
save_graph(G, 'xavier_niel_partners')

In [9]:
degree_centrality = nx.degree_centrality(G)

sorted_degree_centrality = sorted(degree_centrality.items(), key=lambda x: x[1], reverse=True)

sorted_degree_centrality

[('Xavier Niel', 0.3018867924528302),
 ('Memo Bank', 0.1018867924528302),
 ('PayFit', 0.04528301886792453),
 ('Jacques-Antoine Granjon', 0.04528301886792453),
 ('Zefir', 0.03018867924528302),
 ('Resilience (Clinics/Outpatient Services)', 0.03018867924528302),
 ('Thibaud Elziere', 0.03018867924528302),
 ('Zenly', 0.03018867924528302),
 ('SeFaireAider.com', 0.03018867924528302),
 ('Nabla', 0.026415094339622643),
 ('Tracktor', 0.026415094339622643),
 ('Marc Simoncini', 0.026415094339622643),
 ('MWM', 0.026415094339622643),
 ('HrFlow.ai', 0.026415094339622643),
 ('Karos', 0.026415094339622643),
 ('Jérémie Berrebi', 0.026415094339622643),
 ('Brut.', 0.022641509433962266),
 ('Trone', 0.022641509433962266),
 ('Devialet', 0.022641509433962266),
 ('Cozycozy', 0.022641509433962266),
 ('Ambler (Healthcare Services)', 0.022641509433962266),
 ('SmartAngels', 0.022641509433962266),
 ('InMemori', 0.018867924528301886),
 ('Alan', 0.018867924528301886),
 ('Costockage', 0.018867924528301886),
 ('Climb (

In [ ]:
deal_type_groups = data.groupby('Deal Type')
deal_type_data = {deal_type: group for deal_type, group in deal_type_groups}

# Display the keys (Deal Types)
deal_type_data.keys()

dict_keys(['Early Stage VC', 'Later Stage VC', 'Restart - Later VC'])

In [ ]:
for deal_type, df_deal_type in deal_type_data.items():
    print(f'Deal Type: {deal_type}')
    G = create_graph(df_deal_type[['Companies', 'Partners']])
    save_graph(G, f'{deal_type}_graph', 'deal_type')

In [ ]:
vc_round_groups = data.groupby('VC Round')
vc_round_data = {vc_round: group for vc_round, group in vc_round_groups}

# Display the keys (VC Rounds)
vc_round_data.keys()

In [ ]:
for vc_round, df_vc_round in vc_round_data.items():
    print(f'VC Round: {vc_round}')
    G = create_graph(df_vc_round[['Companies', 'Partners']])
    save_graph(G, f'{vc_round}_graph', 'vc_rounds')

In [ ]:
primary_industry_sector_groups = data.groupby('Primary Industry Sector')
primary_industry_sector_data = {sector: group for sector, group in primary_industry_sector_groups}

# Display the keys (Primary Industry Sectors)
primary_industry_sector_data.keys()

In [ ]:
for sector, df_sector in primary_industry_sector_data.items():
    print(f'Primary Industry Sector: {sector}')
    G = create_graph(df_sector[['Companies', 'Partners']])
    save_graph(G, f'{sector}_graph', 'primary_industry_sectors')